In [1]:
import os
from dotenv import load_dotenv
import pandas as pd
import ontology_mapper_new

In [2]:
pd.options.display.max_rows = None  # display all rows
pd.options.display.max_columns = None  # display all columns
pd.set_option('display.max_colwidth', None) # don't truncate wide columns

In [3]:
tier2 = pd.read_csv("../cdes/RADx-rad_tier2_dict_2024-08-22.csv", keep_default_na=False, dtype=str)

In [4]:
tier2.head()

Id  \
0             protocol_id   
1     technology_platform   
2  technology_description   
3    technology_reference   
4     biorecognition_type   

                                                                Label  \
0                    Unique name or identifier for biosensor protocol   
1                          Abbreviation or short label for technology   
2                                     Short description of technology   
3  URL of publication, preprint, or website that describes technology   
4             Type of molecular entity used for biosensor fabrication   

              Examples              Section Cardinality Terms Datatype Unit  \
0     ddPCR_SARS-CoV-2  Technology Metadata      single         string        
1                ddPCR  Technology Metadata      single         string        
2  Droplet Digital PCR  Technology Metadata      single         string        
3                       Technology Metadata      single         string        
4                       Technology Metadata    multiple         string        

                                                                                                                                                                                                                                                                                                                 Enumeration  \
0                                                                                                                                                                                                                                                                                                                              
1                                                                                                                                                                                                                                                                                                                              
2                                                                                                                                                                                                                                                                                                                              
3                                                                                                                                                                                                                                                                                                                              
4  "aptamer"=[aptamer] | "antibody"=[antibody] | "antigen"=[antigen] | "molecular beacon"=[molecular beacon] | "nanobody"=[nanobody] | "primer"=[primer] | "receptor"=[receptor] | "DNA-oligonucleotide"=[DNA-oligonucleotide] | "analyte binding peptide"=[analyte binding peptide] | "enzyme-substrate"=[enzyme-substrate]   

                                                                                             Notes  \
0                                                                        example: ddPCR_SARS-CoV-2   
1                                                                                   example: ddPCR   
2                                                                     example: Droplet Digital PCR   
3                                                                                                    
4  Multiple entities can be specified as list if biosenor uses a combination of molecular entities   

                     MissingValueCodes    Provenance SeeAlso  
0  "-9960"=[Not Entered By Originator]  RADx-rad DCC          
1  "-9960"=[Not Entered By Originator]  RADx-rad DCC          
2  "-9960"=[Not Entered By Originator]  RADx-rad DCC          
3  "-9960"=[Not Entered By Originator]  RADx-rad DCC          
4  "-9960"=[Not Entered By Originator]  RADx-rad DCC

In [5]:
def split_string_variations(input_string):
    # Split the input string by underscores
    parts = input_string.split('_')
    
    # Store all possible substrings
    substrings = set()
    
    # Generate combinations of substrings by slicing the list of parts
    for i in range(len(parts)):
        for j in range(i + 1, len(parts) + 1):
            substrings.add(' '.join(parts[i:j]))  # Join with a space instead of underscore
    
    # Return the result as a list
    return sorted(substrings)

In [6]:
ids = tier2[["Id"]].copy()
ids["keyword"] = ids["Id"].apply(split_string_variations)
ids = ids.explode("keyword")
print(f"Number of kewords: {ids.shape[0]}")
print(f"Number of unique keywords: {ids['keyword'].nunique()}")
keywords = list(ids["keyword"].unique())
ids.head()

Number of kewords: 7210
Number of unique keywords: 2411


Id      keyword
0          protocol_id           id
0          protocol_id     protocol
0          protocol_id  protocol id
1  technology_platform     platform
1  technology_platform   technology

In [7]:
ids[ids["keyword"].str.contains("inchi key")]

Id                           keyword
14   immobilization_reagent_inchi_key  immobilization reagent inchi key
14   immobilization_reagent_inchi_key                         inchi key
14   immobilization_reagent_inchi_key                 reagent inchi key
295               substrate_inchi_key                         inchi key
295               substrate_inchi_key               substrate inchi key

In [8]:
terms = pd.read_csv("../ontology_mappings_2024-09-24.csv")
terms.head()

use   keyword               pref_label  \
0  NaN  protocol                 Protocol   
1  NaN  protocol  procedure specification   
2  NaN  protocol       method development   
3  NaN  protocol                 protocol   
4    y  protocol                 Protocol   

                                                                                                                                           synonyms  \
0                                                                                                                                     ('Protocol',)   
1                                                                                      ('flow specification', 'workflow specification', 'protocol')   
2  ('U44 grant', 'N43 grant', 'N44 grant', 'R43 grant', 'U43 grant', 'protocol', 'R42 grant', 'R44 grant', 'STTR grant', 'SBIR grant', 'R41 grant')   
3                                                                                                                                                ()   
4                                                                             ('Experiment report', 'Experiment metadata', 'Experiment annotation')   

                                                                                                                                                                                                                                         definition  \
0                                                                                                                                                                                     ('A rule which guides how an activity should be performed.',)   
1                                                                                    ('A specification on the order, transitions and trigger of multiple action specifications that are part of some aggregate action specification. [Allotrope]',)   
2                                                                                                         ('development of protocols, procedures, or processes for conducting biomedical research; most often applies to analytical methodology.',)   
3  ('A plan specification which has sufficient level of detail and quantitative information to communicate it between investigation agents, so that different investigation agents will reliably be able to independently reproduce the process.',)   
4                 ('A human-readable collection of information about about how a scientific experiment or analysis was carried out that results in a specific set of data or results used for further analysis or to test a specific hypothesis.',)   

                                                       class  
0  http://ncicb.nci.nih.gov/xml/owl/EVS/Thesaurus.owl#C42651  
1    http://purl.allotrope.org/ontologies/result#AFR:0000938  
2         http://purl.bioontology.org/ontology/CSP/4001-0081  
3                                                OBI:0000272  
4                          http://edamontology.org/data:2531

In [9]:
terms.query("keyword == 'inchi key'")

Empty DataFrame
Columns: [use, keyword, pref_label, synonyms, definition, class]
Index: []

In [10]:
# extra_mappings = [{"use": "y", "keyword": "inchi key", "use": "y", "pref_label": "", "synonyms": "", "definition": "An InChIKey molecular structure is a molecular structure specified as an InChIKey (hashed InChI), which is a fixed length (25 character) condensed digital representation of an InChI chemical structure specification. It uniquely identifies a chemical compound. An InChIKey identifier is not human- nor machine-readable but is more suitable for web searches than an InChI chemical structure specification. [edamontology.org]", "class": ""},
#                   {"use": "y", "immobilization", "keyword": "inchi key", "use": "y", "pref_label": "", "synonyms": "", "definition": "", "class": ""}

In [11]:
mapped_terms = terms.dropna()
print(f"Number of mapped terms: {mapped_terms.shape[0]}")
mapped_terms.head()

Number of mapped terms: 385


use              keyword                   pref_label  \
4    y             protocol                     Protocol   
11   y  technology platform  Technology Platform Version   
12   y          description                  Description   
14   y          description                  Description   
18   y            reference                     Citation   

                                                                                              synonyms  \
4                                ('Experiment report', 'Experiment metadata', 'Experiment annotation')   
11  ('Technology Platform', 'Technology Platform Version', 'Platform Version', 'Platform', 'platform')   
12                        ('Description', 'Descriptive', 'description', 'DESCR', 'Desc', 'Descriptor')   
14                                                                                                  ()   
18                                                            ('Reference', 'Bibliographic reference')   

                                                                                                                                                                                                                                                                                   definition  \
4                                                           ('A human-readable collection of information about about how a scientific experiment or analysis was carried out that results in a specific set of data or results used for further analysis or to test a specific hypothesis.',)   
11                                                                                                                                                  ('The specific version (manufacturer, model, etc.) of a technology that is used to carry out a laboratory or computational experiment.',)   
12                                                                                                                                                                                                  ('A written or verbal account, representation, statement, or explanation of something.',)   
14                                                                                                                                                                                                                          ('The text which is used to provide information about a thing.',)   
18  ('Bibliographic data that uniquely identifies a scientific article, book or other published material.', 'A bibliographic reference might include information such as authors, title, journal name, date and (possibly) a link to the abstract or full-text of the article if available.')   

                                                        class  
4                           http://edamontology.org/data:2531  
11  http://ncicb.nci.nih.gov/xml/owl/EVS/Thesaurus.owl#C45378  
12  http://ncicb.nci.nih.gov/xml/owl/EVS/Thesaurus.owl#C25365  
14                   https://w3id.org/reproduceme#Description  
18                          http://edamontology.org/data:0970

In [12]:
ids = ids.merge(mapped_terms, on="keyword")
print(f"Number of matched terms: {ids.shape[0]}")
ids.head()

Number of matched terms: 2424


Id              keyword use  \
0             protocol_id             protocol   y   
1     technology_platform  technology platform   y   
2  technology_description          description   y   
3  technology_description          description   y   
4    technology_reference            reference   y   

                    pref_label  \
0                     Protocol   
1  Technology Platform Version   
2                  Description   
3                  Description   
4                     Citation   

                                                                                             synonyms  \
0                               ('Experiment report', 'Experiment metadata', 'Experiment annotation')   
1  ('Technology Platform', 'Technology Platform Version', 'Platform Version', 'Platform', 'platform')   
2                        ('Description', 'Descriptive', 'description', 'DESCR', 'Desc', 'Descriptor')   
3                                                                                                  ()   
4                                                            ('Reference', 'Bibliographic reference')   

                                                                                                                                                                                                                                                                                  definition  \
0                                                          ('A human-readable collection of information about about how a scientific experiment or analysis was carried out that results in a specific set of data or results used for further analysis or to test a specific hypothesis.',)   
1                                                                                                                                                  ('The specific version (manufacturer, model, etc.) of a technology that is used to carry out a laboratory or computational experiment.',)   
2                                                                                                                                                                                                  ('A written or verbal account, representation, statement, or explanation of something.',)   
3                                                                                                                                                                                                                          ('The text which is used to provide information about a thing.',)   
4  ('Bibliographic data that uniquely identifies a scientific article, book or other published material.', 'A bibliographic reference might include information such as authors, title, journal name, date and (possibly) a link to the abstract or full-text of the article if available.')   

                                                       class  
0                          http://edamontology.org/data:2531  
1  http://ncicb.nci.nih.gov/xml/owl/EVS/Thesaurus.owl#C45378  
2  http://ncicb.nci.nih.gov/xml/owl/EVS/Thesaurus.owl#C25365  
3                   https://w3id.org/reproduceme#Description  
4                          http://edamontology.org/data:0970

In [13]:
# Define the dictionary for replacements
replacements = {
    "http://ncicb.nci.nih.gov/xml/owl/EVS/Thesaurus.owl#": "Thesaurus:",
    "http://purl.allotrope.org/ontologies/.*#AFR:": "af-p:", # why doesn't this work all the time?
    "http://purl.allotrope.org/ontologies/process#AFP:": "af-p:"
}
ids["class"] = ids["class"].replace(replacements, regex=True)
ids.head(100)

Id                 keyword use  \
0                                   protocol_id                protocol   y   
1                           technology_platform     technology platform   y   
2                        technology_description             description   y   
3                        technology_description             description   y   
4                          technology_reference               reference   y   
5                           biorecognition_type                    type   y   
6                           target_analyte_type                 analyte   y   
7                           target_analyte_type            analyte type   y   
8                           target_analyte_type                    type   y   
9                           target_analyte_name                 analyte   y   
10                          target_analyte_name            analyte name   y   
11                            target_analyte_id                 analyte   y   
12                             signal_detection               detection   y   
13                             signal_detection                  signal   y   
14                                      surface                 surface   y   
15                             measurement_type             measurement   y   
16                             measurement_type                    type   y   
17                           readout_instrument              instrument   y   
18                  immobilization_reagent_name                 reagent   y   
19                  immobilization_reagent_name            reagent name   y   
20                    immobilization_reagent_id                 reagent   y   
21             immobilization_reagent_inchi_key                   inchi   y   
22             immobilization_reagent_inchi_key                 reagent   y   
23                immobilization_reagent_source                 reagent   y   
24                immobilization_reagent_source                  source   y   
25             immobilization_reagent_source_id                 reagent   y   
26             immobilization_reagent_source_id                  source   y   
27            immobilization_reagent_source_url                 reagent   y   
28            immobilization_reagent_source_url                  source   y   
29            immobilization_reagent_source_url                     url   y   
30                  electrochemical_method_name  electrochemical method   y   
31                  electrochemical_method_name                  method   y   
32                  electrochemical_method_name             method name   y   
33            electrochemical_method_instrument  electrochemical method   y   
34            electrochemical_method_instrument              instrument   y   
35            electrochemical_method_instrument                  method   y   
36              electrochemical_method_solution  electrochemical method   y   
37              electrochemical_method_solution                  method   y   
38              electrochemical_method_solution                solution   y   
39       electrochemical_method_solution_source  electrochemical method   y   
40       electrochemical_method_solution_source                  method   y   
41       electrochemical_method_solution_source                solution   y   
42       electrochemical_method_solution_source                  source   y   
43                          reference_electrode               electrode   y   
44                          reference_electrode               reference   y   
45                          reference_electrode     reference electrode   y   
46                          auxiliary_electrode     auxiliary electrode   y   
47                          auxiliary_electrode               electrode   y   
48                            working_electrode               electrode   y   
49                            working_electrode       working electrode   y   
50              

In [14]:
def remove_substrings(keywords):
    keywords = sorted(keywords, key=len, reverse=True)  # Sort by length, longest first
    result = []
    
    for keyword in keywords:
        if not any(keyword in k for k in result):
            result.append(keyword)
    
    return result

In [15]:
# Apply the function to each group in the DataFrame
groups = ids.groupby("Id")["keyword"].apply(list).apply(remove_substrings).reset_index()

In [16]:
# Function to remove substrings and their corresponding classes
def remove_substrings_with_classes(keywords, classes):
    sorted_pairs = sorted(zip(keywords, classes), key=lambda x: len(x[0]), reverse=True)
    result_keywords = []
    result_classes = []
    
    for keyword, cls in sorted_pairs:
        if not any(keyword in k for k in result_keywords):
            result_keywords.append(keyword)
            result_classes.append(cls)
    
    return pd.Series([result_keywords, result_classes])

# Group by Id, aggregate the keywords and classes, and apply the function
grouped = ids.groupby("Id").agg({
    "keyword": list,
    "class": list
}).apply(lambda row: remove_substrings_with_classes(row['keyword'], row['class']), axis=1)

# Reformatting the DataFrame
grouped.columns = ['filtered_keywords', 'filtered_classes']
grouped = grouped.reset_index()

In [17]:
grouped

Id  \
0                                          accumulation_time   
1                                           acquisition_time   
2                                      acquisition_time_unit   
3                                        adsorption_time_max   
4                                        adsorption_time_min   
5                                       adsorption_time_unit   
6                                              age_range_max   
7                                              age_range_min   
8                                           aggregating_site   
9                               analyte_binding_peptide_name   
10                 analyte_binding_peptide_parent_protein_id   
11                analyte_binding_peptide_parent_protein_url   
12              analyte_binding_peptide_reference_protein_id   
13            analyte_binding_peptide_reference_structure_id   
14                          analyte_binding_peptide_sequence   
15                             analytical_cutoff_description   
16                                     analytical_cutoff_max   
17                                analytical_cutoff_max_unit   
18                                     analytical_cutoff_min   
19                                analytical_cutoff_min_unit   
20                                    analytical_inclusivity   
21                                    analytical_sensitivity   
22                               analytical_sensitivity_unit   
23                                     antigen_concentration   
24                                antigen_concentration_unit   
25                                     antigen_cterminal_tag   
26                                 antigen_expression_system   
27                                       antigen_formulation   
28                                                antigen_id   
29                                              antigen_name   
30                                     antigen_nterminal_tag   
31                                            antigen_region   
32                                        antigen_region_end   
33                                      antigen_region_start   
34                                          antigen_sequence   
35                                            antigen_source   
36                                        antigen_source_url   
37                                  area_under_the_roc_curve   
38                                                assay_date   
39                                             assay_readout   
40                                 assay_readout_description   
41                                       assay_readout_error   
42                                        assay_readout_unit   
43                                              assay_result   
44                                        assay_result_other   
45                                       auxiliary_electrode   
46                            backward_inner_primer_sequence   
47                              backward_inner_primer_source   
48                          backward_inner_primer_source_url   
49                             backward_loop_primer_sequence   
50                               backward_loop_primer_source   
51                           backward_loop_primer_source_url   
52                            backward_outer_primer_sequence   
53                              backward_outer_primer_source   
54                          backward_outer_primer_source_url   
55                                       biorecognition_type   
56                                              capacity_mgd   
57                                capture_antibody_clonality   
58                                    capture_antibody_clone   
59                        capture_antibody_expression_system   
60                              capture_antibody_formulation   
61                       capture_antibody_host_organism_name   
62                    capt

In [18]:
grouped["Terms"] = grouped['filtered_classes'].apply(lambda x: ' '.join(x))
grouped = grouped[["Id", "Terms"]].copy()
grouped.head(25)

Id  \
0                                accumulation_time   
1                                 acquisition_time   
2                            acquisition_time_unit   
3                              adsorption_time_max   
4                              adsorption_time_min   
5                             adsorption_time_unit   
6                                    age_range_max   
7                                    age_range_min   
8                                 aggregating_site   
9                     analyte_binding_peptide_name   
10       analyte_binding_peptide_parent_protein_id   
11      analyte_binding_peptide_parent_protein_url   
12    analyte_binding_peptide_reference_protein_id   
13  analyte_binding_peptide_reference_structure_id   
14                analyte_binding_peptide_sequence   
15                   analytical_cutoff_description   
16                           analytical_cutoff_max   
17                      analytical_cutoff_max_unit   
18                           analytical_cutoff_min   
19                      analytical_cutoff_min_unit   
20                          analytical_inclusivity   
21                          analytical_sensitivity   
22                     analytical_sensitivity_unit   
23                           antigen_concentration   
24                      antigen_concentration_unit   

                                                                                             Terms  
0                                                                    NCIT:C120860 Thesaurus:C25207  
1                                                                                     af-p:0001158  
2                                                                    af-p:0001158 Thesaurus:C42574  
3                                                               Thesaurus:C157206 Thesaurus:C25207  
4                                                               Thesaurus:C157206 Thesaurus:C25207  
5                                                               Thesaurus:C157206 Thesaurus:C42574  
6                                                                Thesaurus:C38013 Thesaurus:C25150  
7                                                                Thesaurus:C38013 Thesaurus:C25150  
8                                                                                 Thesaurus:C37901  
9                                                      Thesaurus:C128639 GO:0005488 Thesaurus:C735  
10                                         Thesaurus:C128639 GO:0005488 Thesaurus:C735 NCIT:C17021  
11                            Thesaurus:C128639 GO:0005488 Thesaurus:C735 NCIT:C17021 af-p:0001068  
12       http://edamontology.org/data:0970 Thesaurus:C128639 GO:0005488 Thesaurus:C735 NCIT:C17021  
13  http://edamontology.org/data:0970 Thesaurus:C41186 Thesaurus:C128639 GO:0005488 Thesaurus:C735  
14                 http://purl.bioontology.org/ontology/CSP/2446-2100 Thesaurus:C128639 GO:0005488  
15                                                   Thesaurus:C25365 NCIT:C25391 Thesaurus:C47877  
16                                                                    NCIT:C25391 Thesaurus:C47877  
17                                                         NCIT:C25391 Thesaurus:C47877 UO:0000000  
18                                                                    NCIT:C25391 Thesaurus:C47877  
19                                                         NCIT:C25391 Thesaurus:C47877 UO:0000000  
20                                                                                     NCIT:C25391  
21                                   http://purl.bioontology.org/ontology/MESH/D012680 NCIT:C25391  
22                        http://purl.bioontology.org/ontology/MESH/D012680 NCIT:C25391 UO:0000000  
23                                                                      Thesaurus:C41185 NCIT:C268  
24                                                                            UO:0000051 NCIT:C268

In [19]:
tier2.drop(columns="Terms", inplace=True)
tier2 = tier2.merge(grouped, on="Id", how="left")
tier2.fillna("", inplace=True)

In [20]:
tier2.head(25)

Id  \
0                              protocol_id   
1                      technology_platform   
2                   technology_description   
3                     technology_reference   
4                      biorecognition_type   
5                      target_analyte_type   
6                      target_analyte_name   
7                        target_analyte_id   
8                         signal_detection   
9                                  surface   
10                        measurement_type   
11                      readout_instrument   
12             immobilization_reagent_name   
13               immobilization_reagent_id   
14        immobilization_reagent_inchi_key   
15           immobilization_reagent_source   
16        immobilization_reagent_source_id   
17       immobilization_reagent_source_url   
18             electrochemical_method_name   
19       electrochemical_method_instrument   
20         electrochemical_method_solution   
21  electrochemical_method_solution_source   
22                     reference_electrode   
23                     auxiliary_electrode   
24                       working_electrode   

                                                                                                                                      Label  \
0                                                                                          Unique name or identifier for biosensor protocol   
1                                                                                                Abbreviation or short label for technology   
2                                                                                                           Short description of technology   
3                                                                        URL of publication, preprint, or website that describes technology   
4                                                                                   Type of molecular entity used for biosensor fabrication   
5                                                                                            Type of analyte(s) or target(s) to be detected   
6                                                                                                    Name of target molecule to be detected   
7   Unique identifer for target molecule or biological entity to be detected (e.g., UniProt Id for a protein, NCBI taxonomy Id for viruses)   
8                                                                                          Type of signal generated by the methods or assay   
9                                                                                   Type of plate or electrode used in the methods or assay   
10                                                                      Name of the quantity or quantities being measured by the technology   
11                                                                                                 Instrument used to measure assay readout   
12                                                                                  Reagent used to immobilize a capture probe to a surface   
13                                                          Unique identifier or catalog number of immobilization reagent given by supplier   
14                                                                                                    InChI Key of the immobilization agent   
15                                                                                                                      Supplier of reagent   
16                                                          Unique identifier or catalog number of immobilization reagent given by supplier   
17                                                          URL of supplier catalog page or publication DOI link for immobilization reagent   
18                                                                              Type of electrochemical technique performed to

In [21]:
tier2 = tier2[["Id", "Label", "Examples", "Section", "Cardinality", "Terms", "Datatype", "Unit", "Enumeration", "Notes", "MissingValueCodes", "Provenance", "SeeAlso"]]

In [22]:
tier2

Id  \
0                                                protocol_id   
1                                        technology_platform   
2                                     technology_description   
3                                       technology_reference   
4                                        biorecognition_type   
5                                        target_analyte_type   
6                                        target_analyte_name   
7                                          target_analyte_id   
8                                           signal_detection   
9                                                    surface   
10                                          measurement_type   
11                                        readout_instrument   
12                               immobilization_reagent_name   
13                                 immobilization_reagent_id   
14                          immobilization_reagent_inchi_key   
15                             immobilization_reagent_source   
16                          immobilization_reagent_source_id   
17                         immobilization_reagent_source_url   
18                               electrochemical_method_name   
19                         electrochemical_method_instrument   
20                           electrochemical_method_solution   
21                    electrochemical_method_solution_source   
22                                       reference_electrode   
23                                       auxiliary_electrode   
24                                         working_electrode   
25                                        capture_aptamer_id   
26                                  capture_aptamer_sequence   
27                       capture_aptamer_modification_5prime   
28                  capture_aptamer_modification_5prime_role   
29                       capture_aptamer_modification_3prime   
30                  capture_aptamer_modification_3prime_role   
31                     capture_aptamer_modification_internal   
32                capture_aptamer_modification_internal_role   
33                               capture_aptamer_formulation   
34                                    capture_aptamer_source   
35                                capture_aptamer_source_url   
36                                    capture_aptamer_purity   
37                      capture_aptamer_target_organism_name   
38               capture_aptamer_target_organism_taxonomy_id   
39                   capture_aptamer_target_organism_subtype   
40                       capture_aptamer_target_protein_name   
41                         capture_aptamer_target_protein_id   
42                   capture_aptamer_target_protein_sequence   
43                     capture_aptamer_target_protein_region   
44                                        capture_aptamer_kd   
45                                   capture_aptamer_kd_unit   
46                                       capture_aptamer_kon   
47                                  capture_aptamer_kon_unit   
48                                      capture_aptamer_koff   
49                                 capture_aptamer_koff_unit   
50                                 capture_aptamer_kd_method   
51                                       detector_aptamer_id   
52                                 detector_aptamer_sequence   
53                      detector_aptamer_modification_5prime   
54                 detector_aptamer_modification_5prime_role   
55                      detector_aptamer_modification_3prime   
56                 detector_aptamer_modification_3prime_role   
57                              detector_aptamer_formulation   
58                                   detector_aptamer_source   
59                               detector_aptamer_source_url   
60                                   detector_aptamer_purity   
61                     detector_aptamer_target_organism_name   
62              detector_a

In [23]:
tier2_name = "../cdes/RADx-rad_tier2_dict_2024-09-30.csv"
tier2.to_csv(tier2_name, index=False)